In [1]:
import os
import pandas as pd
from lxml import html
import requests
import re
import sys
from datetime import datetime

from bs4 import BeautifulSoup
from urllib.request import Request, urlopen
import time
import pickle
import string

In [2]:
fund_name = 'vanguard'


CIK_LIST = ['862084', '736054', '888451', '1021882', '857490', '101868', '799127', '52848', '891190', '891190', '791107', '1070414', '106830', '106830', '68138', '788599', '862341', '788606', '105563', '752177', '836906', '889519', '889519', '794105', '794105', '783401', '783401', '791107', '826473', '826473']



In [3]:
cur_wd = os.getcwd()
if 'trunk' in cur_wd:
    output_directory = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'output')
else:
    output_directory = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'output','working')
    
cached_wd = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'cached_data')
cur_wd = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'data')
print('data directory')
print(cur_wd)
print('output directory')
print(output_directory)

print('cached data')
print(cached_wd)


data directory
C:\Users\jjanko\Desktop\wei_mutual_fund_project\data
output directory
C:\Users\jjanko\Desktop\wei_mutual_fund_project\output\working
cached data
C:\Users\jjanko\Desktop\wei_mutual_fund_project\cached_data


In [119]:
weblink = {}
txt = []

for CIK in CIK_LIST:
    weblink[CIK]  = []
    txt_files = os.listdir(os.path.join(cur_wd, CIK, 'nd-30'))
    for i in txt_files:
        txt.append(i)
        weblink[CIK].append(r"https://www.sec.gov/Archives/edgar/data/" + str(CIK)+r"/"  + i)

In [5]:
with open(os.path.join(cached_wd, 'errors_dict_n30D.pickle'), 'rb') as handle:
    errors = pickle.load(handle)
    
print(errors)

{'5007': ['0000909334-00-000113.txt', '0000909334-01-000063.txt', '0000909334-01-500080.txt', '0000909334-02-000039.txt', '0000909334-02-000191.txt', '0000909334-96-000042.txt', '0000909334-96-000143.txt', '0000909334-97-000085.txt', '0000909334-97-000228.txt', '0000909334-98-000071.txt', 'saan30d-063003.txt', 'saan30d-063004.txt', 'saan30d-063005.txt', 'saan30d-12312002.txt', 'saan30d-12312003.txt', 'saan30d-12312004.txt', 'saan30d-12312005.txt', 'saan30d-6302002.txt', '0000909334-00-000028.txt', '0000909334-01-000056.txt', '0000909334-03-000066.txt', '0000909334-03-000316.txt', '0000909334-04-000064.txt', '0000909334-04-000241.txt', '0000909334-05-000049.txt', '0000909334-05-000284.txt', '0000909334-06-000055.txt', '0000909334-99-000021.txt', '0000909334-99-000107.txt', '0001061128-17-000002.txt', '0001061128-17-000033.txt', '0001061128-18-000021.txt', '0001061128-18-000058.txt', '0001061128-19-000002.txt', '0001061128-19-000044.txt'], '1029446': ['sabn30d-063003.txt', 'sabn30d-06300

In [6]:
with open(os.path.join(cached_wd, 'panel2_n30d.pickle'), 'rb') as handle:
    panel2 = pickle.load(handle)
    

In [7]:
panel2 = panel2.loc[panel2['file_read'].isin(txt)]

In [8]:
print(panel2)
panel2.to_csv(os.path.join(output_directory, fund_name + '_panel_2_n30d.csv'), sep = ',')

Empty DataFrame
Columns: [CLASS-CONTRACT-ID, CLASS-CONTRACT-NAME, CLASS-CONTRACT-TICKER-SYMBOL, SERIES-ID, OWNER-CIK, SERIES-NAME, file_read, date_filed, company conformed name, reporting_date]
Index: []


## Test on One FILE

In [111]:

CIK  = '36405'
text =  '0000932471-03-000327.txt'


In [122]:
weblink[CIK]

['https://www.sec.gov/Archives/edgar/data/826473/0000893220-94-000043.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-94-000279.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-94-000474.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-95-000366.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-95-000836.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-96-000891.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-96-001931.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-97-000931.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-97-001850.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-98-001006.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-98-001701.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000893220-99-000647.txt',
 'https://www.sec.gov/Archives/edgar/data/826473/0000932471-00-000567.txt',
 'https://ww

In [10]:
panel2.loc[panel2['file_read'] == text]

Empty DataFrame
Columns: [CLASS-CONTRACT-ID, CLASS-CONTRACT-NAME, CLASS-CONTRACT-TICKER-SYMBOL, SERIES-ID, OWNER-CIK, SERIES-NAME, file_read, date_filed, company conformed name, reporting_date]
Index: []

In [11]:
names = panel2.loc[panel2['file_read'] == text, 'SERIES-NAME']
names = names.unique()
print(names)

[]


In [21]:
def remove_junk(addline):
    addline = re.sub('<[^>]*>', ' ', addline)
    addline = re.sub('&nbsp;', ' ', addline)
    addline = re.sub('&#174;', ' ', addline)
    addline = re.sub('&#8480;', ' ', addline)
    addline = re.sub(r'&reg;',' ',addline)
    addline = re.sub(r'\n', ' ', addline)
    addline = re.sub(r'\t', ' ', addline)
    addline = re.sub('\xa0', ' ', addline)
    return addline

In [112]:
url = r'https://www.sec.gov/Archives/edgar/data/' + CIK + r'/' + text.replace('.txt', '').replace('-','')  + r'/' + text
html_table = urlopen(url).read()
soup = BeautifulSoup(html_table, "html.parser")
txt_file = soup.prettify()
print(txt_file)

lines = soup.prettify().split('\n')
for li in lines:
    if 'CONFORMED PERIOD OF REPORT' in li:
        reporting_date = li.split(':')[1].strip()
        print(reporting_date)
        
    if 'COMPANY CONFORMED NAME' in li:
        conformed_name = li.split(':')[1].strip()
        print(conformed_name)
        
    if 'FILED AS OF DATE' in li:
        date_filed = li.split(':')[1].strip()
        print(date_filed)
        
lines_cleaned = []
for i in lines:
    cleaned_line = remove_junk(i)
    cleaned_line = re.split(r" {2,}", cleaned_line)
    lines_cleaned.append(cleaned_line)
print(lines_cleaned)   
    

-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 SUOeJzjc8BLUgUQk7cK2Vz/kV570LKsC8i0QhahLyILIUh5CHh4m05EcaPZetTrV
 w0tKj0m5xjQ2daUpvjsidQ==
<sec-document>
 0000932471-03-000327.txt : 20030304
 <sec-header>
  0000932471-03-000327.hdr.sgml : 20030304
  <acceptance-datetime>
   20030304110814
ACCESSION NUMBER:		0000932471-03-000327
CONFORMED SUBMISSION TYPE:	N-30D
PUBLIC DOCUMENT COUNT:		1
CONFORMED PERIOD OF REPORT:	20021231
FILED AS OF DATE:		20030304
EFFECTIVENESS DATE:		20030304

FILER:

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			VANGUARD INDEX FUNDS
		CENTRAL INDEX KEY:			0000036405
		IRS NUMBER:				231999755
		STATE OF INCORPORATION:			DE
		FISCAL YEAR END:			1231

	FILING VALUES:
		FORM TYPE:		N-30D
		SEC ACT:		1940 Act
		SEC FILE NUMBER:	811-02652
		FI

[['-----BEGIN PRIVACY-ENHANCED MESSAGE-----'], ['Proc-Type: 2001,MIC-CLEAR'], ['Originator-Name: webmaster@www.sec.gov'], ['Originator-Key-Asymmetric:'], [' MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen'], [' TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB'], ['MIC-Info: RSA-MD5,RSA,'], [' SUOeJzjc8BLUgUQk7cK2Vz/kV570LKsC8i0QhahLyILIUh5CHh4m05EcaPZetTrV'], [' w0tKj0m5xjQ2daUpvjsidQ=='], [' '], [' 0000932471-03-000327.txt : 20030304'], ['', ''], ['', '0000932471-03-000327.hdr.sgml : 20030304'], ['', ''], ['', '20030304110814'], ['ACCESSION NUMBER:', '0000932471-03-000327'], ['CONFORMED SUBMISSION TYPE: N-30D'], ['PUBLIC DOCUMENT COUNT:', '1'], ['CONFORMED PERIOD OF REPORT: 20021231'], ['FILED AS OF DATE:', '20030304'], ['EFFECTIVENESS DATE:', '20030304'], [''], ['FILER:'], [''], [' COMPANY DATA: '], ['', 'COMPANY CONFORMED NAME:', 'VANGUARD INDEX FUNDS'], ['', 'CENTRAL INDEX KEY:', '0000036405'], ['', 'IRS NUMBER:', '231999755'], ['', 'STATE OF INCORPORATION:

In [179]:
def get_legend(df):
    df = df.dropna(axis = 0, how = 'all')
    df = df.dropna(axis = 1, how = 'all')
    legend = pd.DataFrame(columns = ['code', 'symbol', 'restricted'])
    try:
        for count, row in df.iterrows():
            keys = str(row[0])
            code = str(row[1])
            if (keys.strip() != code.strip()) and (code.strip() != ''):
                
                """
                if (len(keys) == 3 and '(' in keys and ')' in keys) or ((len(keys) == 1) and (keys.isdigit() is False) and (keys.isalpha() is False) \
                                                                        and (code.replace(',', '')).isdigit() is False):                
                """
                if (len(keys) == 3 and '(' in keys and ')' in keys):
                    if ~code.replace(',', '').replace(' ', '').isdigit():
                        add = pd.DataFrame([code, keys, '']).T
                        add.columns = ['code', 'symbol', 'restricted']
                        if len(legend.index) == 0:
                            legend = add.copy()
                        else:
                            legend = pd.concat([legend, add], axis = 0,ignore_index = True, sort = False)
    except:
        pass

                    
    return legend

In [138]:


holdings = pd.DataFrame(columns = ['key','holdings name', 'holdings shares', 'holdings value','fund name','identifier'])
legend = pd.DataFrame()
fundname = ''

strip_punct = '!"#$%&\'()+,-./:;<=>?@[\\]^_`{|}'

lines = soup.prettify().split('\n')
for li in lines:
    
    if 'CONFORMED PERIOD OF REPORT' in li:
        reporting_date = li.split(':')[1].strip()
        print(reporting_date)
        
    elif 'COMPANY CONFORMED NAME' in li:
        conformed_name = li.split(':')[1].strip()
        conformed_name = conformed_name.strip(strip_punct).strip().lower()
        print(conformed_name)
        
    elif 'FILED AS OF DATE' in li:
        date_filed = li.split(':')[1].strip()
        print(date_filed)
        
    else:
        cleaned_line = remove_junk(li)
        row = re.split(r" {2,}", cleaned_line)
        
        #get the holdings
        if len(row) == 4:
            
            row[0] = row[0].replace(' ', '')
            row[1] = row[1]
            row[2] = row[2].replace(',','').replace('$','').replace(' ', '')
            row[3] = row[3].replace(',','').replace('$','').replace(' ', '')
            
            checkfound = False
            checkstrings = ['(', ')', '%']
            for s in checkstrings:
                if s in row[2] or s in row[3] or s in row[1] or s in row[0]:
                    checkfound = True
        
            if checkfound is False and len(row[0]) <= 1 and row[2].isdigit() and row[3].isdigit():
                add = pd.DataFrame(row).T
                add.loc[:, 'fund name'] = fundname
                add.loc[:, 'identifier'] = fundname


                add.columns = holdings.columns
                
                if len(holdings.index) > 0:
                    holdings = pd.concat([holdings, add], axis = 0, sort=False, ignore_index = True)
                else:
                    holdings = add.copy()

             
        if len(row) == 1:
            if len(row[0]) > 3:
                key = row[0][0]
                code = row[0][2:]
                
                checkfound = False
                checkstrings = ['-']
                
                for s in checkstrings:
                    if s in key:
                        checkfound = True
                if (row[0][1] == ' ') and (keys.isdigit() is False) and (keys.isalpha() is False) \
                    and (code.replace(',', '').isdigit() is False) \
                    and (checkfound is False) and code not in holdings['holdings name'].unique():
                    print(row)
            
            """
            row = re.split(r'\t+', row[0].rstrip('\t'))
            if len(row) == 2:
                add = pd.DataFrame(row).T
                add_legend = get_legend(add)
                if len(add_legend.index) > 0:
                    add_legend.loc[:, 'identifier'] = fundname
                    if len(legend.index) > 0:
                        legend = pd.concat([legend, add_legend], axis = 0 , sort=False, ignore_index = True)
                    else:
                        legend  = add_legend.copy()            
            
            """


        
print(holdings)
        


20021231
20030304
vanguard index funds
["A table showing the per-share components of the funds' total returns appears on"]
['* Results are for all funds within the same trust.']
['* Freeport-McMoRan Copper &amp;']
['* See Note A in Notes to Financial Statements.']
['* Non-income-producing security.']
['* Clear Channel']
['* Travelers Property Casualty Corp.']
['* WellPoint Health Networks Inc.']
['* Qwest Communications']
['* Federated Department']
['* Total returns do not reflect the $10 annual account maintenance fee applied on']
['* Total returns do not reflect the $10 annual account maintenance fee applied on']
['* Total returns do not reflect the $10 annual account maintenance fee applied on']
['* Berkshire Hathaway Inc.']
['* Travelers Property Casualty']
['* WellPoint Health Networks Inc.']
['* Fox Entertainment Group, Inc.']
['* Qwest Communications']
['* Affiliated Computer Services, Inc.']
['* Federated Department']
['* EchoStar Communications Corp.']
['* Weight Watchers']
['

In [110]:
holdings.to_csv('check.csv')

In [120]:
holdings['value multiplier'] = ''
holdings['textfile'] = text
holdings['CIK'] = CIK
holdings['date_filed'] = '' 
holdings['company conformed name'] = ''
holdings['reporting_date'] = ''

holdings.loc[:, 'date_filed'] = date_filed
holdings.loc[:, 'company conformed name'] = conformed_name
holdings.loc[:, 'reporting_date'] = reporting_date

holdings.index = pd.RangeIndex(len(holdings.index))
print(holdings)

for z in weblink[CIK]:
    if text in z:
        matching_link = z

holdings['weblink'] = matching_link
legend['weblink'] = matching_link
legend['textfile'] = text

     key                       holdings name holdings shares holdings value  \
0                       General Electric Co.        18313442         445932   
1                      Wal-Mart Stores, Inc.         8123209         410303   
2                               Pfizer, Inc.        11340457         346678   
3                      Johnson &amp; Johnson         5466863         293625   
4                             Machines Corp.         3110335         241051   
5                      Merck &amp; Co., Inc.         4132563         233944   
6                   Procter &amp; Gamble Co.         2391130         205494   
7                          The Coca-Cola Co.         4562361         199923   
8                     Verizon Communications         5034700         195095   
9                                Intel Corp.        12192293         189834   
10                  Philip Morris Cos., Inc.         3806990         154297   
11                             PepsiCo, Inc.        

NameError: name 'matching_link' is not defined

In [174]:
legend.loc[:,'restricted'] = 'no'

legend.loc[legend['code'].str.contains("restrict") | legend['code'].str.contains("level 3 security") \
              | legend['code'].str.contains("exempt from registration") |legend['code'].str.contains("private placement") , 'restricted'] = 'yes'

restricted = legend.loc[legend['restricted'].str.contains("yes")]
print(restricted)

holdings.loc[:,'restricted'] = 'no'


                                                 code symbol restricted  \
6   Security exempt from registration under Rule 1...    (d)        yes   
16  Security exempt from registration under Rule 1...    (d)        yes   

         identifier  
6    Destiny ____    
16   Destiny ____    


In [175]:
legend.loc[:,'restricted'] = 'no'

legend.loc[legend['code'].str.contains("restrict") | legend['code'].str.contains("level 3 security") \
              | legend['code'].str.contains("exempt from registration") | legend['code'].str.contains("private placement transaction"), 'restricted'] = 'yes'

restricted = legend.loc[legend['restricted'].str.contains("yes")]
print(restricted)

holdings.loc[:,'restricted'] = 'no'

for index, row in restricted.iterrows():
    holdings.loc[(holdings['identifier'] == row['identifier']) & (holdings['textfile'] == row.textfile) \
                   & (holdings['key'].str.contains(row['symbol'])), 'restricted'] = 'yes'
    
restricted_holdings = holdings.loc[(holdings['restricted'] == 'yes')]

                                                 code symbol restricted  \
6   Security exempt from registration under Rule 1...    (d)        yes   
16  Security exempt from registration under Rule 1...    (d)        yes   

         identifier  
6    Destiny ____    
16   Destiny ____    


AttributeError: 'Series' object has no attribute 'textfile'

In [24]:
def getpanel1(CIK, text, panel2):
    
    url = r'https://www.sec.gov/Archives/edgar/data/' + CIK + r'/' + text.replace('.txt', '').replace('-','')  + r'/' + text
    html_table = urlopen(url).read()
    soup = BeautifulSoup(html_table, "html.parser")
    tags = soup.find_all(['tr','b'])

    names = panel2.loc[panel2['file_read'] == text, 'SERIES-NAME']
    names = names.unique()

    holdings = pd.DataFrame()
    legend = pd.DataFrame()
    fundname = ''

    for tr in tags:
        if 'series' in str(tr).lower() and 'portfolio'  in str(tr).lower() and '<b>' in str(tr).lower():
            s = str(tr).replace('&amp','and')
            s = s.replace('  ', '')
            s = s.replace(';','')
            s = remove_junk(s)
            for n in names:
                if n.lower().strip() in str(s).lower().strip():
                    fundname = n
                    print(fundname)

        td = tr.find_all('td')
        row = [tr.text.strip() for tr in td]
        row = list(filter(None, row))
        if len(row) == 3:
            add = pd.DataFrame(row).T
            cleaned_df, add1 = get_holdings(add)
            if len(cleaned_df.index) > 0:
                cleaned_df.loc[:, 'fund name'] = fundname
                cleaned_df.loc[:, 'identifier'] = fundname
                if len(holdings.index) > 0:
                    holdings = pd.concat([holdings, cleaned_df], axis = 0, sort=False, ignore_index = True)
                else:
                    holdings = cleaned_df.copy()

        if len(row) == 2:
            add = pd.DataFrame(row).T
            add_legend = get_legend(add)
            if len(add_legend.index) > 0:
                add_legend.loc[:, 'identifier'] = fundname
                if len(legend.index) > 0:
                    legend = pd.concat([legend, add_legend], axis = 0 , sort=False, ignore_index = True)
                else:
                    legend  = add_legend.copy()
                    
                    
                    
    holdings['value multiplier'] = ''
    holdings['textfile'] = text
    holdings['CIK'] = CIK
    holdings['date_filed'] = '' 
    holdings['company conformed name'] = ''
    holdings['reporting_date'] = ''

    try:
        date_filed = panel2.loc[panel2['file_read'] == text, 'date_filed'].unique()[0]
        conformed_name = panel2.loc[panel2['file_read'] == text, 'company conformed name'].unique()[0]
        reporting_date = panel2.loc[panel2['file_read'] == text, 'reporting_date'].unique()[0]
    except IndexError:
        date_filed = ''
        conformed_name = ''

    holdings.loc[:, 'date_filed'] = date_filed
    holdings.loc[:, 'company conformed name'] = conformed_name
    holdings.loc[:, 'reporting_date'] = reporting_date

    holdings.index = pd.RangeIndex(len(holdings.index))
    print(holdings)

    legend['weblink'] = url
    legend['textfile'] = text
    
    return holdings, legend

    

In [26]:
holdings, legend = getpanel1('726735', '0001193125-15-388874.txt', panel2)

Government and Quality Bond Portfolio
Asset Allocation Portfolio
Growth and Income Portfolio
Growth Portfolio
Capital Appreciation Portfolio
Natural Resources Portfolio
SA BlackRock Multi-Asset Income Portfolio
Strategic Multi-Asset Portfolio
    holdings shares holdings value  \
0               146           9621   
1             38895         344999   
2               177           7871   
3             16315         278334   
4              4311         564525   
5              1731         358854   
6              2529         419688   
7              3151         344278   
8                78           6383   
9               126           6091   
10             2212         199744   
11               36           7647   
12              153           6717   
13             1340          98021   
14              132           5927   
15           121708         331045   
16              220          18775   
17             7437         590869   
18              336          13047 

In [27]:
holdings.to_csv(os.path.join(output_directory, fund_name + '_test_holdings2.csv'), sep = ',')
legend.to_csv(os.path.join(output_directory, fund_name + '_test_legend2.csv'), sep = ',')
print(holdings)

    holdings shares holdings value  \
0               146           9621   
1             38895         344999   
2               177           7871   
3             16315         278334   
4              4311         564525   
5              1731         358854   
6              2529         419688   
7              3151         344278   
8                78           6383   
9               126           6091   
10             2212         199744   
11               36           7647   
12              153           6717   
13             1340          98021   
14              132           5927   
15           121708         331045   
16              220          18775   
17             7437         590869   
18              336          13047   
19             8566         359172   
20              378          16961   
21              345          13124   
22              198          10504   
23             4100         128535   
24              275           7959   
25          

# Run on all CIKs

In [28]:
panel1 = pd.DataFrame()


panel1 = pd.DataFrame()
panel1_legend = pd.DataFrame()
error_panel1 = []
no_holdings = {}

CIK_LIST = ['726735']

for CIK in CIK_LIST:
    no_holdings[CIK] = []
    txt_files = os.listdir(os.path.join(cur_wd, CIK, 'n-q'))
    for i in txt_files:
        if '.csv' not in i and i not in errors[CIK]:
            holdings, legend = getpanel1(str(CIK), str(i), panel2)
            print(holdings)
            if len(holdings) == 0:
                no_holdings[CIK].append(i)

            if panel1.empty:
                panel1 = holdings.copy()
                panel1_legend = legend.copy()
            else:
                panel1 = pd.concat([panel1, holdings], axis = 0, sort = False)
                panel1_legend = pd.concat([panel1_legend , legend], axis = 0, sort = False)

            panel1.index = pd.RangeIndex(len(panel1.index))


Asset Allocation Portfolio
Multi-Asset Portfolio
Multi-Asset Portfolio
Strategic Multi-Asset Portfolio
     holdings shares holdings value  \
0             400000         399863   
1               2800         151620   
2               3000         117630   
3               3600         281088   
4               1050          54337   
5               6300         302211   
6               7600         137256   
7               1200          43188   
8               3000         149430   
9               2500         119975   
10              4400         268092   
11               450          40653   
12              4500         206775   
13              8400         245448   
14              1700          45543   
15             14100         112095   
16              4100          32472   
17              7200         118368   
18             23600          59129   
19              1300          53508   
20              4821         125009   
21              6800         492524   


Money Market Portfolio
Asset Allocation Portfolio
Growth Portfolio
Capital Appreciation Portfolio
Natural Resources Portfolio
Multi-Asset Portfolio
Multi-Asset Portfolio
Strategic Multi-Asset Portfolio
     holdings shares holdings value  \
0              10000         224400   
1               3000         148290   
2                875          57374   
3               7300         416976   
4               8400         196392   
5               1125          46429   
6               2925         212384   
7               2500         175225   
8               4400         323884   
9               4650         554977   
10              4500         249795   
11              8650         249985   
12              1500          61845   
13             14600         133006   
14              4100          43706   
15              7700         169169   
16             23600          66919   
17              4000         120600   
18              1410          74067   
19              11

Asset Allocation Portfolio
Multi-Asset Portfolio
Strategic Multi-Asset Portfolio
     holdings shares holdings value  \
0               2360         143087   
1               7600         347396   
2               8800         175384   
3               1175          46788   
4              12905         858699   
5                900          41168   
6               4600         662584   
7               5500         273845   
8              12675         404586   
9               1525          77821   
10             16000         100320   
11              3600          48492   
12              8300         206172   
13               955          55810   
14              6200         502324   
15              4500         220860   
16              4959          25539   
17              6500         443560   
18              9000         395963   
19             64675        1583891   
20              2000          66200   
21              4450         109425   
22             16000  

Money Market Portfolio
Government and Quality Bond Portfolio
Asset Allocation Portfolio
Growth and Income Portfolio
     holdings shares holdings value  \
0               1500         106080   
1               6000         482400   
2               2410         151131   
3              12200         620614   
4               8800         225896   
5               3025         156423   
6                900          56268   
7               1255         171671   
8               4000         289040   
9               5100         300543   
10               800          93520   
11              6212         223694   
12             17900         547740   
13              3799         240933   
14             17700         114342   
15              8868         106859   
16              8715         200358   
17              1783         105946   
18              7100         699563   
19             10740          55848   
20             63570        1612135   
21              6900      

Money Market Portfolio
Government and Quality Bond Portfolio
Asset Allocation Portfolio
Growth and Income Portfolio
Growth Portfolio
Capital Appreciation Portfolio
Natural Resources Portfolio
Multi-Asset Portfolio
Multi-Asset Portfolio
Strategic Multi-Asset Portfolio
    holdings shares holdings value  \
0              1100          57024   
1              6012         436712   
2              2814         146778   
3             12091         494159   
4             10100         161095   
5              2850         139251   
6              1125          55395   
7              1050         129560   
8              4000         240160   
9              4500         194490   
10             6412         159082   
11             2824         158963   
12            17700          52392   
13             8868          71121   
14             8715         168897   
15              258          11971   
16             6034         733252   
17            10640          58733   
18        

...

Government and Quality Bond Portfolio
Asset Allocation Portfolio
Growth and Income Portfolio
Growth Portfolio
Capital Appreciation Portfolio
Natural Resources Portfolio
SA BlackRock Multi-Asset Income Portfolio
Strategic Multi-Asset Portfolio
    holdings shares holdings value                       holdings name   key  \
0               125          10625                 Omnicom Group, Inc.         
1             38895         242705                         Aimia, Inc.         
2             14271         269294                 Publicis Groupe ADR         
3              4895         644867                          Boeing Co.         
4               181          43390               Lockheed Martin Corp.         
5              2357         504280              Northrop Grumman Corp.         
6               780         106182                        Raytheon Co.         
7                95           8012              Rockwell Collins, Inc.         
8              2212         238741   

Government and Quality Bond Portfolio
Asset Allocation Portfolio
Growth and Income Portfolio
Growth Portfolio
Capital Appreciation Portfolio
Natural Resources Portfolio
SA BlackRock Multi-Asset Income Portfolio
Strategic Multi-Asset Portfolio
    holdings shares holdings value  \
0              8311        1469883   
1               266          40565   
2               780          86791   
3            100000         293000   
4             16743        1544039   
5              2500         280625   
6              6112         280908   
7              6565         360878   
8              4160         273978   
9             10786         932989   
10            14534         809980   
11             2154          94065   
12            15000         493500   
13            40000         770400   
14             5325         196527   
15             6652         447014   
16            11501        1176092   
17            12401         535227   
18             9372         575441 

SA BlackRock Multi-Asset Income Portfolio
    holdings shares holdings value  \
0              6426        1633553   
1             96846         278916   
2             22952        1750549   
3              2500         311325   
4              6220         299928   
5              6184         393117   
6             25019        1863665   
7              6876         762274   
8              2166         103405   
9             16000         505920   
10            40000         779600   
11             4672         192871   
12             5982         432738   
13             1795         150762   
14            10176        1257754   
15            14448         771234   
16            88863         792658   
17             7353         472430   
18             4478         215168   
19              879          78301   
20             7270         690068   
21             9108         544476   
22             9798          98862   
23             4604          81537   
24      

SA Wellington Government and Quality Bond Portfolio
SA Edge Asset Allocation Portfolio
SA Wellington Growth and Income Portfolio
SA Wellington Growth Portfolio
SA Wellington Capital Appreciation Portfolio
SA Wellington Natural Resources Portfolio
SA BlackRock Multi-Asset Income Portfolio
SA Wellington Strategic Multi-Asset Portfolio
    holdings shares holdings value  \
0              1810         631907   
1            106846         292758   
2             10696         662724   
3              2000         257260   
4              6205         340096   
5              1331          51510   
6              4757         352589   
7             19461        1776206   
8              3777         564699   
9             14000         440580   
10            40000         827000   
11             2485         112952   
12             6195         409923   
13             1445          86353   
14             8581        1252311   
15              499          27260   
16            14523

SA Wellington Government and Quality Bond Portfolio
SA PGI Asset Allocation Portfolio
SA Wellington Growth and Income Portfolio
SA Wellington Growth Portfolio
SA Wellington Capital Appreciation Portfolio
SA Wellington Natural Resources Portfolio
SA BlackRock Multi-Asset Income Portfolio
SA Wellington Strategic Multi-Asset Portfolio
    holdings shares holdings value  \
0               495          52688   
1              1755         556984   
2             77000         215600   
3             12194         839679   
4              5500         439120   
5              6544         378440   
6              1273          51047   
7              2213         206805   
8             17966        2054771   
9              2599         354192   
10             9000         325170   
11            36000         673380   
12             2769         107767   
13             6128         417869   
14             1878          73824   
15            11320         981218   
16             1403 

In [29]:
panel1.loc[:,'acq name'] = ''
panel1.loc[:,'acq date'] = ''
panel1.loc[:,'acq cost'] = ''
print(output_directory)
panel1.to_csv(os.path.join(output_directory, fund_name + '_panel1.csv'), sep = ',')
panel1_legend.to_csv(os.path.join(output_directory, fund_name + '_panel1_legend.csv'), sep = ',')

C:\Users\jjanko\Desktop\wei_mutual_fund_project\output\working


In [30]:

panel1_legend.loc[:,'restricted'] = 'no'

panel1_legend.loc[panel1_legend['code'].str.contains("restrict") | panel1_legend['code'].str.contains("level 3 security") \
              | panel1_legend['code'].str.contains("exempt from registration") |panel1_legend['code'].str.contains("private placement") , 'restricted'] = 'yes'

restricted = panel1_legend.loc[panel1_legend['restricted'].str.contains("yes")]

restricted.to_csv(os.path.join(output_directory, fund_name + '_panel1_restricted_legend.csv'), sep = ',')
print(restricted)

panel1.loc[:,'restricted'] = 'no'

for index, row in restricted.iterrows():
    try:
        panel1.loc[(panel1['identifier'] == row['identifier']) & (panel1['textfile'] == row.textfile) \
                       & (panel1['key'].str.contains(row['symbol'])), 'restricted'] = 'yes'
    except:
        pass
    
restricted_holdings = panel1.loc[(panel1['restricted'] == 'yes')]
restricted_holdings.to_csv(os.path.join(output_directory, fund_name + '_panel1_restricted.csv'), sep = ',')

                                                 code symbol restricted  \
3   Securities exempt from registration under Rule...      *        yes   
14  Securities exempt from registration under Rule...      *        yes   
17  Securities exempt from registration under Rule...      *        yes   
23  Securities exempt from registration under Rule...      *        yes   
4   Securities exempt from registration under Rule...      *        yes   
11  Securities exempt from registration under Rule...      *        yes   
33  Securities exempt from registration under Rule...      *        yes   
39  Securities exempt from registration under Rule...      *        yes   
3   Securities exempt from registration under Rule...      *        yes   
10  Securities exempt from registration under Rule...      *        yes   
34  Securities exempt from registration under Rule...      *        yes   
40  Securities exempt from registration under Rule...      *        yes   
45  Securities exempt fro

C:\Users\jjanko\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:16: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  app.launch_new_instance()
